<a href="https://colab.research.google.com/github/niccronc/TV-Show-Recommender/blob/master/IMDb_scraper.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [ ]:
path='/content/drive/My Drive/Colab Notebooks/data/IMDb'

In [ ]:
import requests
import dill
from bs4 import BeautifulSoup
#from datetime import datetime

In [ ]:
url = 'https://www.imdb.com/search/title/?title_type=tv_series,tv_miniseries&user_rating=6.0,&num_votes=100,&view=simple&count=250&start=1&ref_=adv_nxt'
headers = { 'user-agent' : 'TDI', 'Accept-Language': 'en-US,en;q=0.8' }
page = requests.get(url, headers=headers) # Use requests.get to download the page.
page.status_code

200

In [ ]:
soup = BeautifulSoup(page.text, "lxml")

In [ ]:
soup.prettify()

'<!DOCTYPE html>\n<html xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://ogp.me/ns#">\n <head>\n  <script type="text/javascript">\n   var ue_t0=ue_t0||+new Date();\n  </script>\n  <script type="text/javascript">\n   window.ue_ihb = (window.ue_ihb || window.ueinit || 0) + 1;\nif (window.ue_ihb === 1) {\n\nvar ue_csm = window,\n    ue_hob = +new Date();\n(function(d){var e=d.ue=d.ue||{},f=Date.now||function(){return+new Date};e.d=function(b){return f()-(b?0:d.ue_t0)};e.stub=function(b,a){if(!b[a]){var c=[];b[a]=function(){c.push([c.slice.call(arguments),e.d(),d.ue_id])};b[a].replay=function(b){for(var a;a=c.shift();)b(a[0],a[1],a[2])};b[a].isStub=1}};e.exec=function(b,a){return function(){try{return b.apply(this,arguments)}catch(c){ueLogError(c,{attribution:a||"undefined",logLevel:"WARN"})}}}})(ue_csm);\n\n\n    var ue_err_chan = \'jserr\';\n(function(d,e){function h(f,b){if(!(a.ec>a.mxe)&&f){a.ter.push(f);b=b||{};var c=f.logLevel||b.logLevel;c&&c!==k&&c!==m&&c!==n&&c!==p||a

In [ ]:
shows=soup.find_all('span', attrs={'class':'lister-item-header'})
#<span class="field-content"> includes both the names of the parties and their dates
len(shows)

250

In [ ]:
show_names = [show.select('a')[0].text for show in shows]
len(show_names)

250

In [ ]:
show_names[10:20]

['Kingdom',
 'Lucifer',
 'Vikings',
 'The Walking Dead',
 'Breaking Bad',
 'The 100',
 'Community',
 'Vikingane',
 'Agents of S.H.I.E.L.D.',
 'Criminal Minds']

In [ ]:
links = [show.select('a')[0]['href'] for show in shows]
len(links)

250

In [ ]:
links[2]

'/title/tt4236770/?ref_=adv_li_tt'

In [ ]:
show_url = 'https://www.imdb.com'+links[2]
show_url

'https://www.imdb.com/title/tt4236770/?ref_=adv_li_tt'

In [ ]:
#url = 'https://www.imdb.com/search/title/?title_type=tv_series,tv_miniseries&user_rating=6.0,&num_votes=100,&view=simple&count=250&start=1&ref_=adv_nxt'
#headers = { 'user-agent' : 'TDI' }
show_page = requests.get(show_url, headers=headers) # Use requests.get to download the page.
show_page.status_code

200

In [ ]:
show_soup = BeautifulSoup(show_page.text, "lxml")
show_title = show_soup.find('div',attrs = {'class': 'title_wrapper'})
title = show_title.select('h1')[0].text

In [ ]:
title

'Yellowstone\xa0            '

In [ ]:
show_genres = show_title.find('div',attrs = {'class': 'subtext'})

In [ ]:
show_genres.select('a')

[<a href="/search/title?genres=drama&amp;explore=title_type,genres&amp;ref_=tt_ov_inf">Drama</a>,
 <a href="/search/title?genres=western&amp;explore=title_type,genres&amp;ref_=tt_ov_inf">Western</a>,
 <a href="/title/tt4236770/releaseinfo?ref_=tt_ov_inf" title="See more release dates">TV Series (2018– )
 </a>]

In [ ]:
genres = [x.text for x in show_genres.select('a') if 'genres' in x['href']]

In [ ]:
genres

['Drama', 'Western']

In [ ]:
rating = show_soup.find('span', attrs = {'itemprop':'ratingValue'}).text
float(rating)

8.5

In [ ]:
reviews = show_soup.find('span', attrs = {'itemprop':'ratingCount'}).text
reviews

'18,996'

In [ ]:
storyline = show_soup.find('div',attrs = {'id':'titleStoryLine'})
storyline.find('div', attrs = {'class':'inline canwrap'}).select('span')[0].text

"    Yellowstone follows the Dutton family, led by John Dutton, who controls the largest contiguous ranch in the United States, under constant attack by those it borders - land developers, an Indian reservation, and America's first National Park. It is an intense study of a violent world far from media scrutiny - where land grabs make developers billions, and politicians are bought and sold by the world's largest oil and lumber corporations. Where drinking water poisoned by fracking wells and unsolved murders are not news: they are a consequence of living in the new frontier. It is the best and worst of America seen through the eyes of a family that represents both."

In [ ]:
def get_show_info(url):
  show_url = 'https://www.imdb.com'+url
  show_page = requests.get(show_url, headers=headers)
  show_soup = BeautifulSoup(show_page.text, "lxml")
  
  show_title = show_soup.find('div',attrs = {'class': 'title_wrapper'})
  #title = show_title.select('h1')[0].text

  show_genres = show_title.find('div',attrs = {'class': 'subtext'})
  genres = [x.text for x in show_genres.select('a') if 'genres' in x['href']]

  rating = show_soup.find('span', attrs = {'itemprop':'ratingValue'}).text
  reviews = show_soup.find('span', attrs = {'itemprop':'ratingCount'}).text

  show_storyline = show_soup.find('div',attrs = {'id':'titleStoryLine'})
  storyline = show_storyline.find('div', attrs = {'class':'inline canwrap'}).select('span')[0].text

  return [genres, rating, reviews, storyline]

In [ ]:
get_show_info(links[7])

('Shameless\xa0            ',
 ['Comedy', 'Drama'],
 '8.6',
 '191,948',
 '    Watch the Irish American family the Gallaghers dealing with their alcoholic father Frank. Fiona, the eldest daughter, takes the role of the parent to her five brothers and sisters. Lip, Ian, Debbie, Carl, and Liam deal with life on the South Side of Chicago. Fiona balances her sex life and raising her siblings. Every episode is another crazy situation that one or more of the Gallagher six get into. Watch them grow and learn how to make their way in life with what little they have.')

In [ ]:
def get_show_data(show):
  name = show.select('a')[0].text
  link = show.select('a')[0]['href']

  return [name]+get_show_info(link)


In [ ]:
get_show_data(shows[4])

['Game of Thrones',
 ['Action', 'Adventure', 'Drama'],
 '9.3',
 '1,696,027',
 '    In the mythical continent of Westeros, several powerful families fight for control of the Seven Kingdoms. As conflict erupts in the kingdoms of men, an ancient enemy rises once again to threaten them all. Meanwhile, the last heirs of a recently usurped dynasty plot to take back their homeland from across the Narrow Sea.']

In [ ]:
data=[]

url = 'https://www.imdb.com/search/title/?title_type=tv_series,tv_miniseries&user_rating=6.0,&num_votes=100,&view=simple&count=250&start=1&ref_=adv_nxt'
page = requests.get(url, headers=headers)

soup = BeautifulSoup(page.text, "lxml")
shows=soup.find_all('span', attrs={'class':'lister-item-header'})

for show in shows:
  data.append(get_show_data(show))

In [ ]:
data

250

In [ ]:
list_url='https://www.imdb.com/search/title/'
params={'title_type':'tv_series,tv_miniseries',
        'user_rating':'6.0,',
        'num_votes':'100,',
        'view':'simple',
        'count':250,
        'start':1,
        'ref_':'adv_nxt'}

page_test=requests.get(list_url, params = params, headers = headers)
page_test.status_code

200

In [ ]:
soup_test = BeautifulSoup(page_test.text, "lxml")
shows_test=soup_test.find_all('span', attrs={'class':'lister-item-header'})
len(shows_test)

250

In [ ]:
total_pages = 38+1
initial='https://www.imdb.com/search/title/'
def get_page_args(i):
  params={'title_type':'tv_series',
        'user_rating':'6.0,',
        'num_votes':'250,',
        'view':'simple',
        'count':250,
        'start':250*i+1,
        'ref_':'adv_nxt'}

  return {"url": initial,"params": params}

In [ ]:
def get_links(response):
  soup = BeautifulSoup(response.text, "lxml")
    
  shows=soup.find_all('span', attrs={'class':'lister-item-header'})

  return [ (show.select('a')[0].text, show.select('a')[0]['href']) for show in shows]

In [ ]:
!pip install requests-futures

  Created wheel for requests-futures: filename=requests_futures-1.0.0-cp36-none-any.whl size=7013 sha256=6ff2251437573060199bc9fd4f20ff0cbb4ad5f471118bf4f452496ffc888b13
  Stored in directory: /root/.cache/pip/wheels/26/d0/f5/dc4e4a37bbe55c9acf967d2bd899152412c1e49c227f5395ff
Successfully built requests-futures


In [ ]:
from requests_futures.sessions import FuturesSession

session = FuturesSession(max_workers=5)
futures = [session.get(headers = headers, **get_page_args(i)) for i in range(total_pages)]
all_links = [pair for future in futures for pair in get_links(future.result())]
#all_links contains pairs (name, link) for every show with the required qualifications

In [ ]:
len(all_links)

9649

In [ ]:
import dill
dill.dump(all_links, open(path+'/all_links.pkd', 'wb'))

In [ ]:
links_list = dill.load(open(path+'/all_links.pkd', 'rb'))

In [ ]:
len(links_list)

9649

In [ ]:
links_list[4][1].split('/')[-2]

'tt0944947'

In [ ]:
get_show_info(links_list[23][1])

[['Comedy', 'Drama', 'Romance'],
 '8.4',
 '336,258',
 "    Told from the perspective of an unseen documentary filmmaker, the series offers an honest, often-hilarious perspective of family life. Parents Phil and Claire yearn for an honest, open relationship with their three kids, but a daughter who is trying to grow up too fast, another who is too smart for her own good, and a rambunctious young son make it challenging. Claire's dad Jay and his Latina wife Gloria are raising two sons together, but people sometimes believe Jay to be Gloria's father. Jay's gay son Mitchell and his partner Cameron have adopted a little Asian girl, completing one big -- straight, gay, multicultural, traditional -- happy family."]

In [ ]:
!pip install ediblepickle

  Created wheel for ediblepickle: filename=ediblepickle-1.1.3-cp36-none-any.whl size=7549 sha256=080f7253e70b789c49e39dc1a8bbf71b980bfe7ef03286ee46d22d9e3fab56da
  Stored in directory: /root/.cache/pip/wheels/a4/c1/0d/114a961dbcf46cca9d6e81b28289f6720422cfc6f2319dd6dc
Successfully built ediblepickle


In [ ]:
from ediblepickle import checkpoint
from retrying import retry

In [ ]:
@retry(stop_max_attempt_number=5)
def get_the_page(url):
    page = requests.get(url, headers=headers) # Use requests.get to download the page.
    if page.status_code != 200:
        #raise ConnectionError('Error loading the page')
        return None
    else:
        return page.text


In [ ]:
@checkpoint(key=lambda args, kwargs: args[1].split(/)[-2] + '.p', work_dir=path)
def get_show_info(name,url):
  text=get_the_page('https://www.imdb.com'+url)
  if text is None:
    return []
  show_soup = BeautifulSoup(text, "lxml")
  
  show_title = show_soup.find('div',attrs = {'class': 'title_wrapper'})
  #title = show_title.select('h1')[0].text

  show_genres = show_title.find('div',attrs = {'class': 'subtext'})
  genres = [x.text for x in show_genres.select('a') if 'genres' in x['href']]

  rating = show_soup.find('span', attrs = {'itemprop':'ratingValue'}).text
  reviews = show_soup.find('span', attrs = {'itemprop':'ratingCount'}).text

  show_storyline = show_soup.find('div',attrs = {'id':'titleStoryLine'})
  storyline = show_storyline.find('div', attrs = {'class':'inline canwrap'}).select('span')[0].text

  return [name, genres, rating, reviews, storyline]

In [ ]:
def get_show_info2(response):

  show_soup=BeautifulSoup(response.text,'lxml')
  
  show_title = show_soup.find('div',attrs = {'class': 'title_wrapper'})
  #title = show_title.select('h1')[0].text

  show_genres = show_title.find('div',attrs = {'class': 'subtext'})
  genres = [x.text for x in show_genres.select('a') if 'genres' in x['href']]

  rating = show_soup.find('span', attrs = {'itemprop':'ratingValue'}).text
  reviews = show_soup.find('span', attrs = {'itemprop':'ratingCount'}).text

  show_storyline = show_soup.find('div',attrs = {'id':'titleStoryLine'}).find('div', attrs = {'class':'inline canwrap'})
  if show_storyline is not None:
    storyline = show_storyline.select('span')[0].text
  else:
    storyline = ''

  return [genres, rating, reviews, storyline]

In [ ]:
all_data=[]

for show in links_list:
  all_data.append(get_show_info(*show))

In [ ]:
len(all_data)

533

In [ ]:
session2 = FuturesSession(max_workers=5)

futures = [session2.get(url = 'https://www.imdb.com'+show[1], headers = headers) for show in links_list]
the_data = [data for future in futures for data in get_show_info2(future.result())]

In [ ]:
num_shows = len(links_list)

In [ ]:
mydata = [ [the_data[4*i],the_data[4*i+1],the_data[4*i+2],the_data[4*i+3]] for i in range(num_shows) ]

In [ ]:
allthedata = [[links_list[i][0], the_data[4*i],the_data[4*i+1],the_data[4*i+2],the_data[4*i+3]] for i in range(num_shows)]

In [ ]:
len(allthedata)

9649

In [ ]:
allthedata[1]

['Dark',
 ['Crime', 'Drama', 'Mystery'],
 '8.8',
 '237,507',
 "    The first German production from the world's leading Internet TV Network is set in a German town in present day where the disappearance of two young children exposes the double lives and fractured relationships among four families. In ten hour-long episodes, the story takes on a surprising twist that ties back to the same town in 1986."]

In [ ]:
dill.dump(allthedata, open(path+'/all_data.pkd', 'wb'))

In [ ]:
import pandas as pd

In [ ]:
df = pd.DataFrame(allthedata, columns = ['Name','Genres','Score','Votes','Storyline'])

In [ ]:
df.head()

Name  ...                                          Storyline
0  The Umbrella Academy  ...      On the same day in October 1989, forty-thr...
1                  Dark  ...      The first German production from the world...
2           Yellowstone  ...      Yellowstone follows the Dutton family, led...
3           Perry Mason  ...      Set in 1932 Los Angeles, the series focuse...
4       Game of Thrones  ...      In the mythical continent of Westeros, sev...

[5 rows x 5 columns]

In [ ]:
df.to_csv(path+'/storyline.csv', index=False)